In [3]:
import pandas as pd

def list_wikipedia_sp500() -> pd.DataFrame:
    # Ref: https://stackoverflow.com/a/75845569/
    url = 'https://en.m.wikipedia.org/wiki/List_of_S%26P_500_companies'
    return pd.read_html(url, attrs={'id': 'constituents'}, index_col='Symbol')[0]
def list_wikipedia_nq100() -> pd.DataFrame:
    # Ref: https://stackoverflow.com/a/75845569/
    url = 'https://en.wikipedia.org/wiki/Nasdaq-100#Components'
    return pd.read_html(url, attrs={'id': 'constituents'}, index_col='Ticker')[0]


In [4]:
nq100 = list_wikipedia_nq100()
nq100.index
sp500 = list_wikipedia_sp500()

In [7]:
import yfinance as yf
tickerstrings = sp500.index.values.tolist()

for ticker in tickerstrings:
    data = yf.download(ticker, period="max", actions=True, repair=True, auto_adjust=True, threads=4, group_by="Ticker")
    data = data.reset_index().drop(columns=['Stock Splits','Repaired?','Date'])
    data.to_csv(f'data/SP500/{ticker}.csv')  # ticker_AAPL.csv for example

C:\Users\roman\Documents\QF\MarketMine\yfinance\scrapers\history.py:875: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Repaired?"] = False
[*********************100%%**********************]  1 of 1 completed
C:\Users\roman\Documents\QF\MarketMine\yfinance\scrapers\history.py:875: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Repaired?"] = False
[*********************100%%**********************]  1 of 1 completed
C:\Users\roman\Documents\QF\MarketMine\yfinance\scrapers\history.py:875: SettingWithCopy

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
C:\Users\roman\Documents\QF\MarketMine\yfinance\scrapers\history.py:875: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Repaired?"] = False
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
C:\Users\roman\Documents\QF\MarketMine\yfinance\scrapers\history.py:875: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_ind

KeyError: "['Stock Splits', 'Repaired?'] not found in axis"

# Preprocessing data

In [9]:
import glob
max_len = 500

for csv in glob.glob('./data/SP500/*.csv'):
    ticker = csv.split('\\')[-1].split('.')[0]
    df=pd.read_csv(csv)
    if len(df) < max_len:
        continue
    for idx in range(0, len(df), max_len):
        if idx + max_len > len(df):
            windowed_data = df.iloc[len(df)-max_len:].reset_index()
        else:
            windowed_data = df.iloc[idx:idx+max_len].reset_index()
        assert len(windowed_data) == max_len
        train_test_type = 'TEST' if idx + max_len > len(df) else 'TRAIN'
        windowed_data.to_csv(f'preprocessed/SP500/{ticker+str(idx)}_{train_test_type}.csv')
            

# Transformer


In [54]:
!python mvts_transformer/src/main.py --output_dir experiments --comment "pretraining through imputation" --name market_pretrained --records_file Imputation_records.xls --data_dir preprocessed/ --data_class market --pattern TRAIN --val_ratio 0.2 --epochs 1000 --lr 0.0005 --optimizer RAdam --batch_size 64 --pos_encoding learnable --d_model 128


Evaluating Epoch 0   0.0% | batch:         0 of         2	|	loss: 390.058
Evaluating Epoch 0  50.0% | batch:         1 of         2	|	loss: 385.848
Training Epoch 1   0.0% | batch:         0 of         7	|	loss: 1.73485
Training Epoch 1  14.3% | batch:         1 of         7	|	loss: 1.67163
Training Epoch 1  28.6% | batch:         2 of         7	|	loss: 1.77368
Training Epoch 1  42.9% | batch:         3 of         7	|	loss: 1.86242
Training Epoch 1  57.1% | batch:         4 of         7	|	loss: 1.68687
Training Epoch 1  71.4% | batch:         5 of         7	|	loss: 1.61967
Training Epoch 1  85.7% | batch:         6 of         7	|	loss: 1.58898

Evaluating Epoch 1   0.0% | batch:         0 of         2	|	loss: 1.55055
Evaluating Epoch 1  50.0% | batch:         1 of         2	|	loss: 1.57135
Training Epoch 2   0.0% | batch:         0 of         7	|	loss: 1.30839
Training Epoch 2  14.3% | batch:         1 of         7	|	loss: 1.58461
Training Epoch 2  28.6% | batch:         2 of         7

2024-03-10 22:16:30,333 | INFO : Loading packages ...
2024-03-10 22:16:33,599 | INFO : Stored configuration file in 'experiments\market_pretrained_2024-03-10_22-16-33_3uI'
2024-03-10 22:16:33,599 | INFO : Running:
mvts_transformer/src/main.py --output_dir experiments --comment pretraining through imputation --name market_pretrained --records_file Imputation_records.xls --data_dir preprocessed/ --data_class market --pattern TRAIN --val_ratio 0.2 --epochs 1000 --lr 0.0005 --optimizer RAdam --batch_size 64 --pos_encoding learnable --d_model 128

2024-03-10 22:16:33,615 | INFO : Using device: cuda
2024-03-10 22:16:33,616 | INFO : Loading and preprocessing data ...
2024-03-10 22:16:33,655 | INFO : Loading 1271 datasets files using 16 parallel processes ...
2024-03-10 22:16:33,754 | INFO : Loading packages ...
2024-03-10 22:16:33,755 | INFO : Loading packages ...
2024-03-10 22:16:33,762 | INFO : Loading packages ...
2024-03-10 22:16:33,762 | INFO : Loading packages ...
2024-03-10 22:16:33,76

In [3]:
!python mvts_transformer/src/main.py --output_dir experiments --comment "finetune for distribution pred e^nll" --name market_pretrained --records_file Regression_records.xls --data_dir preprocessed/ --data_class market --pattern TRAIN --val_pattern TEST  --epochs 2000 --lr 0.001 --optimizer RAdam --pos_encoding learnable --d_model 128 --load_model experiments/market_pretrained_2024-03-10_22-16-33_3uI/checkpoints/model_best.pth --task distribution --change_output --batch_size 128


Loaded model from experiments/market_pretrained_2024-03-10_22-16-33_3uI/checkpoints/model_best.pth. Epoch: 764
Evaluating Epoch 0   0.0% | batch:         0 of         4	|	loss: 0.0141894
Evaluating Epoch 0  25.0% | batch:         1 of         4	|	loss: 0.0141894
Evaluating Epoch 0  50.0% | batch:         2 of         4	|	loss: 0.0141894
Evaluating Epoch 0  75.0% | batch:         3 of         4	|	loss: 0.0141894
Training Epoch 1   0.0% | batch:         0 of         4	|	loss: 0.0141894
Training Epoch 1  25.0% | batch:         1 of         4	|	loss: 0.0141893
Training Epoch 1  50.0% | batch:         2 of         4	|	loss: 0.0141892
Training Epoch 1  75.0% | batch:         3 of         4	|	loss: 0.0141891
Epoch 1 Training Summary: epoch: 1.000000 | loss: 0.014189 | 
Evaluating Epoch 1   0.0% | batch:         0 of         4	|	loss: 0.014189
Evaluating Epoch 1  25.0% | batch:         1 of         4	|	loss: 0.014189
Evaluating Epoch 1  50.0% | batch:         2 of         4	|	loss: 0.014189
Ev

2024-03-13 13:36:12,008 | INFO : Loading packages ...
2024-03-13 13:36:15,528 | INFO : Stored configuration file in 'experiments\market_pretrained_2024-03-13_13-36-15_kPp'
2024-03-13 13:36:15,528 | INFO : Running:
mvts_transformer/src/main.py --output_dir experiments --comment finetune for distribution pred e^nll --name market_pretrained --records_file Regression_records.xls --data_dir preprocessed/ --data_class market --pattern TRAIN --val_pattern TEST --epochs 2000 --lr 0.001 --optimizer RAdam --pos_encoding learnable --d_model 128 --load_model experiments/market_pretrained_2024-03-10_22-16-33_3uI/checkpoints/model_best.pth --task distribution --change_output --batch_size 128

2024-03-13 13:36:15,548 | INFO : Using device: cuda
2024-03-13 13:36:15,548 | INFO : Loading and preprocessing data ...
2024-03-13 13:36:15,603 | INFO : Loading 1271 datasets files using 16 parallel processes ...
2024-03-13 13:36:15,703 | INFO : Loading packages ...
2024-03-13 13:36:15,703 | INFO : Loading pack

In [ ]:
!python mvts_transformer/src/main.py --output_dir experiments --comment "test trained model" --name market_test1 --records_file test_records.xls --data_dir preprocessed/SP500/ --data_class market --epochs 200 --pos_encoding learnable --d_model 128 --load_model experiments/market_pretrained_2024-03-13_13-36-15_kPp/checkpoints/model_best.pth --task distribution --change_output --batch_size 128 --test_ratio 0.5  --val_ratio 0.1 --test_only testset


# Making quantitative rankings

In [1]:
from mvts_transformer.src import rank
import torch

In [2]:
e = rank.Engine('models/nq100.pth')

TSTransformerEncoderDistregressor(
  (project_inp): Linear(in_features=6, out_features=128, bias=True)
  (pos_enc): LearnablePositionalEncoding(
    (dropout): Dropout(p=0.0, inplace=False)
  )
  (transformer_encoder): TransformerEncoder(
    (layers): ModuleList(
      (0-2): 3 x TransformerBatchNormEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=256, bias=True)
        (dropout): Dropout(p=0.0, inplace=False)
        (linear2): Linear(in_features=256, out_features=128, bias=True)
        (norm1): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (norm2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (dropout1): Dropout(p=0.0, inplace=False)
        (dropout2): Dropout(p=0.0, inplace=False)
      )
    )
  )
  (dropout1): Dropout(p=0.

C:\Users\roman\anaconda3\envs\QF\lib\site-packages\torch\nn\modules\transformer.py:218: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because self.layers[0] was not TransformerEncoderLayer
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


In [3]:
import yfinance as yf
tickerstrings = ['AAPL','NVDA', 'MSFT', 'GOOG', 'NFLX', 'AMZN', 'TSLA']
data = {}
for ticker in tickerstrings:
    ticker_data = yf.download(ticker, period="max", actions=True, repair=True, auto_adjust=True, threads=4, group_by="Ticker")
    ticker_data = ticker_data.reset_index().drop(columns=['Stock Splits','Repaired?','Date'])
    data[ticker] = ticker_data

2024-05-18 14:02:05,341 | INFO : price-repair-split: No 100x errors detected
2024-05-18 14:02:05,448 | INFO : price-repair-100x: No sporadic 100x errors
2024-05-18 14:02:05,451 | INFO : price-repair-split: No bad splits detected
2024-05-18 14:02:05,454 | INFO : price-repair-missing: No price=0 errors to repair
[*********************100%%**********************]  1 of 1 completed
2024-05-18 14:02:05,678 | INFO : price-repair-split: No 100x errors detected
2024-05-18 14:02:05,683 | INFO : price-repair-100x: No sporadic 100x errors
2024-05-18 14:02:05,687 | INFO : price-repair-split: No bad splits detected
2024-05-18 14:02:05,689 | INFO : price-repair-missing: No price=0 errors to repair
[*********************100%%**********************]  1 of 1 completed
2024-05-18 14:02:06,021 | INFO : price-repair-split: No 100x errors detected
2024-05-18 14:02:06,027 | INFO : price-repair-100x: No sporadic 100x errors
2024-05-18 14:02:06,030 | INFO : price-repair-split: No bad splits detected
2024-05-1

In [5]:
print(e.rank(input=data,steps=1))

{'AAPL': 0.13431832194328308, 'NVDA': 0.3011818528175354, 'MSFT': 0.5874969363212585, 'GOOG': 0.0, 'NFLX': 0.10448984056711197, 'AMZN': 0.12025446444749832, 'TSLA': 1.0}
